#####Libraries
***

In [1]:
import sklearn
import seaborn as sns
import pandas as pd
import numpy as np
import seaborn as sns
!pip install yfinance --upgrade --no-cache-dir
import yfinance as yf
from pandas_datareader import data as pdr
yf.pdr_override()
# pip install TA-lib
# !wget http://prdownloads.sourceforge.net/ta-lib/ta-lib-0.4.0-src.tar.gz

# !tar -xzf ta-lib-0.4.0-src.tar.gz
# %cd ta-lib/
# !./configure --prefix=$HOME
# !make
# !make install

# !TA_LIBRARY_PATH=~/lib TA_INCLUDE_PATH=~/include pip install ta-lib
# import talib as ta
import matplotlib.pyplot as plt
from collections import Counter
from collections import defaultdict

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 62 kB 32.3 MB/s 
  Attempting uninstall: requests
    Found existing installation: requests 2.23.0
    Uninstalling requests-2.23.0:
      Successfully uninstalled requests-2.23.0


In [2]:
from collections import Counter
from collections import defaultdict

#####Load Dataset
***

In [4]:
#φτιάχνω τη λίστα με τα assets μου -> 50 μετοχές 
#διόρθωση : θα βγάλω τυχαία άλλες 4 μετοχές μαζί με την OGN επειδή δεν έχει το ίδιο μέγεθος με τις άλλες 
#βγάζω OGN ,WRK,HST,CE,ACN
assets= ["ABBV","AEP","AIZ","ALLE","AMAT","AMP","AMZN","AVB","AVY",   
  "AXP","BDX","BF-B","BMY","BR","CARR","CDW","CHTR","CNC",   
  "CNP","COP","CTAS","CZR","DG","DPZ","DRE","DXC","META","FTV",   
  "GOOG","GPC","HIG","JPM","KR","PG","PPL","PRU",   
  "PYPL","RE","ROL","ROST","UNH","URI","V","VRSK","XOM"]
  #άρα πρέπει να κατεβάσουμε όλα τα adj close για όλες τις τιμές όλων των μετοχών και να κάνουμε απόλυτο ranking και σε 5 κλασεις (targets)
r=pd.DataFrame(index=pdr.get_data_yahoo(assets[0],'2021-05-29','2022-09-25')['Adj Close'].index)
#παίρνω τιμές για ένα χρόνο και 3 μήνες
for i in assets:
  # print('i metoxi me onoma:',i,'exei megethos',pdr.get_data_yahoo(i,'2021-01-01','2022-04-01')['Adj Close'].count())
  temp= pdr.get_data_yahoo(i,'2021-05-29','2022-09-25')['Adj Close']
  temp=temp.dropna()
  r[i]=temp.values

[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%********

In [5]:
#φτιάχνω ένα αντίγραφο με τις τιμές για να το έχω 
rd=pd.DataFrame(r)
rd

ABBV         AEP         AIZ        ALLE        AMAT  \
Date                                                                     
2021-06-01  106.605827   81.597748  158.413406  136.604294  136.802200   
2021-06-02  105.836273   82.125122  156.835632  135.604462  137.594055   
2021-06-03  106.605827   82.422371  159.030823  135.212372  134.990845   
2021-06-04  106.748329   82.489479  159.834396  136.084763  138.425507   
2021-06-07  107.365868   82.144295  159.295395  135.271179  137.554459   
...                ...         ...         ...         ...         ...   
2022-09-12  142.240005  105.180000  163.490005  100.773888   96.300003   
2022-09-13  138.529999  102.199997  158.490005   95.476807   90.389999   
2022-09-14  139.550003  103.320000  155.919998   94.739998   90.639999   
2022-09-15  142.509995  100.190002  155.759995   93.150002   88.919998   
2022-09-16  144.059998  100.360001  154.830002   89.690002   88.870003   

                   AMP        AMZN         AVB         AVY         AXP  ...  \
Date                                                                    ...   
2021-06-01  256.874268  160.932495  203.371292  218.499512  161.456635  ...   
2021-06-02  257.275818  161.699493  205.369476  215.377533  161.811584  ...   
2021-06-03  258.382568  159.350494  205.707352  215.249908  162.205963  ...   
2021-06-04  259.939728  160.311005  204.404205  216.300385  162.679199  ...   
2021-06-07  259.401062  159.900497  204.780655  212.471527  163.586243  ...   
...                ...         ...         ...         ...         ...  ...   
2022-09-12  289.239990  136.449997  214.220001  192.050003  162.449997  ...   
2022-09-13  277.720001  126.820000  207.850006  184.669998  155.350006  ...   
2022-09-14  277.959991  128.550003  205.080002  180.190002  156.300003  ...   
2022-09-15  277.350006  126.279999  201.320007  179.360001  156.130005  ...   
2022-09-16  272.260010  123.529999  201.979996  173.369995  153.080002  ...   

                   PRU        PYPL          RE        ROL        ROST  \
Date                                                                    
2021-06-01  102.610245  259.269989  252.286011  33.223026  120.749817   
2021-06-02  102.156342  262.170013  249.654388  33.380478  118.805550   
2021-06-03  102.345459  257.790009  249.566986  32.563683  117.322830   
2021-06-04  102.544052  263.040009  251.868454  32.662086  117.313004   
2021-06-07  102.194160  260.600006  250.334167  32.278297  117.347450   
...                ...         ...         ...        ...         ...   
2022-09-12   99.760002   97.650002  282.829987  36.259998   94.980003   
2022-09-13   95.790001   95.010002  279.480011  35.930000   89.860001   
2022-09-14   94.080002   97.660004  280.149994  36.330002   89.459999   
2022-09-15   92.540001   96.400002  285.019989  35.799999   89.559998   
2022-09-16   91.919998   94.000000  283.070007  35.570000   90.250000   

                   UNH         URI           V        VRSK        XOM  
Date                                                                   
2021-06-01  398.641083  339.450012  224.728760  169.534714  56.981377  
2021-06-02  397.788361  338.470001  227.733383  171.020264  57.433758  
2021-06-03  399.856415  336.119995  226.196365  170.178467  57.659946  
2021-06-04  397.582550  332.070007  228.209320  170.990570  57.914417  
2021-06-07  392.299591  316.019989  229.379425  166.187195  57.537430  
...                ...         ...         ...         ...        ...  
2022-09-12  531.250000  313.399994  206.630005  192.509048  97.610001  
2022-09-13  513.960022  294.670013  199.669998  185.940002  95.330002  
2022-09-14  509.769989  290.000000  199.410004  185.910004  97.669998  
2022-09-15  522.909973  288.709991  195.369995  183.979996  94.830002  
2022-09-16  521.020020  286.040009  193.300003  184.429993  93.209999  

[328 rows x 45 columns]

In [6]:
rd1= rd.pct_change().shift(-1)
rd1

ABBV       AEP       AIZ      ALLE      AMAT       AMP  \
Date                                                                     
2021-06-01 -0.007219  0.006463 -0.009960 -0.007319  0.005788  0.001563   
2021-06-02  0.007271  0.003619  0.013997 -0.002891 -0.018919  0.004302   
2021-06-03  0.001337  0.000814  0.005053  0.006452  0.025444  0.006027   
2021-06-04  0.005785 -0.004185 -0.003372 -0.005979 -0.006293 -0.002072   
2021-06-07 -0.005929 -0.031516  0.005537  0.007246 -0.022379 -0.003587   
...              ...       ...       ...       ...       ...       ...   
2022-09-12 -0.026083 -0.028332 -0.030583 -0.052564 -0.061371 -0.039828   
2022-09-13  0.007363  0.010959 -0.016216 -0.007717  0.002766  0.000864   
2022-09-14  0.021211 -0.030294 -0.001026 -0.016783 -0.018976 -0.002195   
2022-09-15  0.010876  0.001697 -0.005971 -0.037144 -0.000562 -0.018352   
2022-09-16       NaN       NaN       NaN       NaN       NaN       NaN   

                AMZN       AVB       AVY       AXP  ...       PRU      PYPL  \
Date                                                ...                       
2021-06-01  0.004766  0.009825 -0.014288  0.002198  ... -0.004424  0.011185   
2021-06-02 -0.014527  0.001645 -0.000593  0.002437  ...  0.001851 -0.016707   
2021-06-03  0.006028 -0.006335  0.004880  0.002918  ...  0.001940  0.020365   
2021-06-04 -0.002561  0.001842 -0.017702  0.005576  ... -0.003412 -0.009276   
2021-06-07  0.020669 -0.005233  0.008548  0.003556  ... -0.000092  0.009785   
...              ...       ...       ...       ...  ...       ...       ...   
2022-09-12 -0.070575 -0.029736 -0.038428 -0.043706  ... -0.039796 -0.027035   
2022-09-13  0.013641 -0.013327 -0.024259  0.006115  ... -0.017852  0.027892   
2022-09-14 -0.017659 -0.018334 -0.004606 -0.001088  ... -0.016369 -0.012902   
2022-09-15 -0.021777  0.003278 -0.033397 -0.019535  ... -0.006700 -0.024896   
2022-09-16       NaN       NaN       NaN       NaN  ...       NaN       NaN   

                  RE       ROL      ROST       UNH       URI         V  \
Date                                                                     
2021-06-01 -0.010431  0.004739 -0.016102 -0.002139 -0.002887  0.013370   
2021-06-02 -0.000350 -0.024469 -0.012480  0.005199 -0.006943 -0.006749   
2021-06-03  0.009222  0.003022 -0.000084 -0.005687 -0.012049  0.008899   
2021-06-04 -0.006092 -0.011750  0.000294 -0.013288 -0.048333  0.005127   
2021-06-07  0.005353  0.009756  0.008807  0.003723  0.026011  0.003156   
...              ...       ...       ...       ...       ...       ...   
2022-09-12 -0.011844 -0.009101 -0.053906 -0.032546 -0.059764 -0.033683   
2022-09-13  0.002397  0.011133 -0.004451 -0.008152 -0.015848 -0.001302   
2022-09-14  0.017384 -0.014589  0.001118  0.025776 -0.004448 -0.020260   
2022-09-15 -0.006842 -0.006425  0.007704 -0.003614 -0.009248 -0.010595   
2022-09-16       NaN       NaN       NaN       NaN       NaN       NaN   

                VRSK       XOM  
Date                            
2021-06-01  0.008763  0.007939  
2021-06-02 -0.004922  0.003938  
2021-06-03  0.004772  0.004413  
2021-06-04 -0.028091 -0.006509  
2021-06-07  0.010131  0.017690  
...              ...       ...  
2022-09-12 -0.034123 -0.023358  
2022-09-13 -0.000161  0.024546  
2022-09-14 -0.010381 -0.029077  
2022-09-15  0.002446 -0.017083  
2022-09-16       NaN       NaN  

[328 rows x 45 columns]

In [7]:
#first: ranks assigned in order they appear in the array
rd2=rd1.rank(axis=1,method='first')
rd2=rd2.dropna()
rd2.astype(int)
jk=rd2.copy()
jk.astype(int)

ABBV  AEP  AIZ  ALLE  AMAT  AMP  AMZN  AVB  AVY  AXP  ...  PRU  \
Date                                                              ...        
2021-06-01    10   32    5     9    31   24    30   38    3   25  ...   12   
2021-06-02    37   33   41    15     2   35     4   24   19   30  ...   27   
2021-06-03    15   13   29    34    45   30    31    4   28   20  ...   17   
2021-06-04    38   20   23    17    15   28    26   32    3   37  ...   22   
2021-06-07     8    1   28    32     2   13    44    9   33   23  ...   19   
...          ...  ...  ...   ...   ...  ...   ...  ...  ...  ...  ...  ...   
2022-09-09    22   19    5    39     4   27    41    7   20   42  ...   34   
2022-09-12    35   30   27     8     4   13     3   29   17   11  ...   14   
2022-09-13    34   36    7    17    29   26    40   10    4   32  ...    5   
2022-09-14    42    2   32    16     9   30    14   12   28   31  ...   17   
2022-09-15    43   34   25     2    31   14     8   38    4   12  ...   23   

            PYPL  RE  ROL  ROST  UNH  URI   V  VRSK  XOM  
Date                                                      
2021-06-01    39   4   29     2   15   14  41    36   35  
2021-06-02     3  20    1     5   36    9  11    13   34  
2021-06-03    44  36   21    10    5    2  35    27   26  
2021-06-04    12  16    8    31    7    1  36     2   14  
2021-06-07    36  27   35    34   24   45  22    38   43  
...          ...  ..  ...   ...  ...  ...  ..   ...  ...  
2022-09-09    37  10   17    38   35   24  23    18   30  
2022-09-12    33  44   45     7   23    5  21    20   37  
2022-09-13    44  28   37    20   15    8  24    25   43  
2022-09-14    20  40   18    35   44   29   8    24    3  
2022-09-15     5  21   24    42   29   20  18    36   15  

[327 rows x 45 columns]

In [8]:
def rank_data(df1):
  for i in range(len(df1.index)):
    d=df1.loc[df1.index[i]]  #της κάθε μέρας d[1] δίνει μόνο τις τιμές 
    #print(d)
    d=d.sort_values()
    d[0:9]=1
    d[9:18]=2
    d[18:27]=3
    d[27:36]=4
    d[36:45]=5
    df1.loc[df1.index[i]]=d
    #print(df1.loc[df1.index[i]])
    #print(d)
  df1=df1.astype(int)
  return df1
r5=rd2.copy()
rd3=rank_data(r5)
rd3

ABBV  AEP  AIZ  ALLE  AMAT  AMP  AMZN  AVB  AVY  AXP  ...  PRU  \
Date                                                              ...        
2021-06-01     2    4    1     1     4    3     4    5    1    3  ...    2   
2021-06-02     5    4    5     2     1    4     1    3    3    4  ...    3   
2021-06-03     2    2    4     4     5    4     4    1    4    3  ...    2   
2021-06-04     5    3    3     2     2    4     3    4    1    5  ...    3   
2021-06-07     1    1    4     4     1    2     5    1    4    3  ...    3   
...          ...  ...  ...   ...   ...  ...   ...  ...  ...  ...  ...  ...   
2022-09-09     3    3    1     5     1    3     5    1    3    5  ...    4   
2022-09-12     4    4    3     1     1    2     1    4    2    2  ...    2   
2022-09-13     4    4    1     2     4    3     5    2    1    4  ...    1   
2022-09-14     5    1    4     2     1    4     2    2    4    4  ...    2   
2022-09-15     5    4    3     1     4    2     1    5    1    2  ...    3   

            PYPL  RE  ROL  ROST  UNH  URI  V  VRSK  XOM  
Date                                                     
2021-06-01     5   1    4     1    2    2  5     4    4  
2021-06-02     1   3    1     1    4    1  2     2    4  
2021-06-03     5   4    3     2    1    1  4     3    3  
2021-06-04     2   2    1     4    1    1  4     1    2  
2021-06-07     4   3    4     4    3    5  3     5    5  
...          ...  ..  ...   ...  ...  ... ..   ...  ...  
2022-09-09     5   2    2     5    4    3  3     2    4  
2022-09-12     4   5    5     1    3    1  3     3    5  
2022-09-13     5   4    5     3    2    1  3     3    5  
2022-09-14     3   5    2     4    5    4  1     3    1  
2022-09-15     1   3    3     5    4    3  2     4    2  

[327 rows x 45 columns]

#####Functions
***

In [9]:
def RPS_calculation(hist_data, submission, asset_no=44):
    # print('check')
    if hist_data.shape[0]<=asset_no:
        return np.nan    
    # print('check')
    asset_id = pd.unique(hist_data.symbol)
    
    for i in range(len(pd.unique(hist_data.date))):
        if len(hist_data[hist_data.date == pd.unique(hist_data.date)[i]])<len(asset_id):
            for asset in [x for x in asset_id if x not in hist_data[hist_data.date == pd.unique(hist_data.date)[i]].symbol.values]:
                right_price = hist_data[hist_data.symbol==asset].sort_values(by='date')
                right_price = right_price[right_price.date <= pd.unique(hist_data.date)[i]]
                right_price = right_price.price.iloc[-1]
                hist_data = hist_data.append({'date' : pd.unique(hist_data.date)[i],
                                               'symbol' : asset,
                                               'price' : right_price}, ignore_index=True)

    #Compute percentage returns
    asset_id = sorted(asset_id) 

    #Compute percentage returns
    returns = pd.DataFrame(columns = ["ID", "Return"])
    
    min_date = min(hist_data.date)
    max_date = max(hist_data.date)
    # max_date = np.max(hist_data.date)
    
    for i in range(0,len(asset_id)):
        temp = hist_data.loc[hist_data.symbol==asset_id[i]]
        
        open_price = float(temp.loc[temp.date==min_date].price)
        close_price = float(temp.loc[temp.date==max_date].price)
        
        returns = returns.append({'ID': temp.symbol.iloc[0], 
                                'Return': (close_price - open_price)/open_price}, ignore_index=True)

    #Define the relevant position of each asset
    ranking = pd.DataFrame(columns=["ID", "Position", "Return"])
    ranking.ID = list(asset_id)
    ranking.Return = returns.Return
    ranking.Position = ranking.Return.rank(method = 'min')

    #Handle Ties
    Series_per_position = pd.DataFrame(columns=["Position","Series", "Rank", "Rank1", "Rank2","Rank3", "Rank4", "Rank5"])
    Series_per_position.Position = list(pd.unique(ranking.Position.sort_values(ascending=True)))
    temp = ranking.Position.value_counts()
    temp = pd.DataFrame(zip(temp.index, temp), columns = ["Rank", "Occurencies"])
    temp = temp.sort_values(by = ["Rank"],ascending=True)
    Series_per_position.Series = list(temp.Occurencies)
    Series_per_position

    total_ranks = Series_per_position.Position.values[-1]
    for i in range(0,Series_per_position.shape[0]):
    
        start_p = Series_per_position.Position[i]
        end_p = Series_per_position.Position[i] + Series_per_position.Series[i]
        temp = pd.DataFrame(columns = ["Position","Rank", "Rank1", "Rank2", "Rank3", "Rank4","Rank5"])
        temp.Position = list(range(int(start_p),int(end_p)))

        if(temp.loc[temp.Position.isin(list(range(1,int(0.2*total_ranks+1))))].empty==False):
            temp.loc[temp.Position.isin(list(range(1,int(0.2*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(1,int(0.2*total_ranks+1))))].assign(Rank=1)
            temp.loc[temp.Position.isin(list(range(1,int(0.2*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(1,int(0.2*total_ranks+1))))].assign(Rank1=1.0)

        elif(temp.loc[temp.Position.isin(list(range(int(0.2*total_ranks+1),int(0.4*total_ranks+1))))].empty==False):
            temp.loc[temp.Position.isin(list(range(int(0.2*total_ranks+1),int(0.4*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.2*total_ranks+1),int(0.4*total_ranks+1))))].assign(Rank=2)
            temp.loc[temp.Position.isin(list(range(int(0.2*total_ranks+1),int(0.4*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.2*total_ranks+1),int(0.4*total_ranks+1))))].assign(Rank2=1.0)

        elif(temp.loc[temp.Position.isin(list(range(int(0.4*total_ranks+1),int(0.6*total_ranks+1))))].empty==False):
            temp.loc[temp.Position.isin(list(range(int(0.4*total_ranks+1),int(0.6*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.4*total_ranks+1),int(0.6*total_ranks+1))))].assign(Rank=3)
            temp.loc[temp.Position.isin(list(range(int(0.4*total_ranks+1),int(0.6*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.4*total_ranks+1),int(0.6*total_ranks+1))))].assign(Rank3=1.0)

        elif(temp.loc[temp.Position.isin(list(range(int(0.6*total_ranks+1),int(0.8*total_ranks+1))))].empty==False):
            temp.loc[temp.Position.isin(list(range(int(0.6*total_ranks+1),int(0.8*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.6*total_ranks+1),int(0.8*total_ranks+1))))].assign(Rank=4)
            temp.loc[temp.Position.isin(list(range(int(0.6*total_ranks+1),int(0.8*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.6*total_ranks+1),int(0.8*total_ranks+1))))].assign(Rank4=1.0)

        elif(temp.loc[temp.Position.isin(list(range(int(0.8*total_ranks+1),int(total_ranks+1))))].empty==False):
            temp.loc[temp.Position.isin(list(range(int(0.8*total_ranks+1),int(total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.8*total_ranks+1),int(total_ranks+1))))].assign(Rank=5)
            temp.loc[temp.Position.isin(list(range(int(0.8*total_ranks+1),int(total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.8*total_ranks+1),int(total_ranks+1))))].assign(Rank5=1.0)
        temp = temp.fillna(0)
        Series_per_position.iloc[i,2:Series_per_position.shape[1]] = temp.mean(axis = 0).iloc[1:temp.shape[1]]

    Series_per_position = Series_per_position.drop('Series', axis = 1)
    ranking = pd.merge(ranking,Series_per_position, on = "Position")
    ranking = ranking[["ID", "Return", "Position", "Rank", "Rank1", "Rank2", "Rank3", "Rank4", "Rank5"]]
    ranking = ranking.sort_values(["Position"])
    # print(ranking)
    #Evaluate submission
    rps_sub = []
    #for aid in list((pd.unique(ranking.ID))):
    for aid in asset_id:

        target = np.cumsum(ranking.loc[ranking.ID==aid].iloc[:,4:9].values).tolist()
        frc = np.cumsum(submission.loc[submission.ID==aid].iloc[:,1:6].values).tolist()
        rps_sub.append(np.mean([(a - b)**2 for a, b in zip(target, frc)]))
    submission["RPS"] = rps_sub
    
    output = {'RPS' : np.mean(rps_sub),
              'details' : submission}
    
    return(output)

In [54]:
#Αυτή η συνάρτηση παίρνει τα data και κάνει τη dummy μέτρηση για το διάστημα ενός χρόνου (όσο οριστεί στην ουσία το insample) για μια μετοχή
n=dict() 
def dummy(st,i,p):
  flag=False
  insample=st.iloc[p:-i]
  print('arxi insample',insample.head(1),'kai telos insample',insample.tail(2),'mikos',len(insample))
  if(len(insample)!=15):
    print('---------------------------------------------------------------',flag)
  count=defaultdict(int)
  for word in insample.values:
    count[word]+=1
  print(word,count)
  count=sorted(count.items()) #list Η πρώτη τιμή είναι η κλάση και η δεύτερη πόσες φορές είδα τον αριθμό.
  temp=[]
  for k in range(5):
    flag=True
    for l in count:
      if(l[0]==k+1):
        temp.append(l[1]/len(insample))
        flag=False
        break
    if(flag):
      temp.append(0)
  # print(temp,count)
  data={
      'prediction':temp
  }
  forecast=pd.DataFrame(data)
  return forecast
# #για όλες τις μετοχές υπολογίζεται το counter τους
dummy(rd3['ABBV'],60,248)


arxi insample Date
2022-05-24    5
Name: ABBV, dtype: int64 kai telos insample Date
2022-06-17    5
2022-06-21    5
Name: ABBV, dtype: int64 mikos 19
--------------------------------------------------------------- False
5 defaultdict(<class 'int'>, {5: 8, 1: 3, 2: 6, 3: 1, 4: 1})


prediction
0    0.157895
1    0.315789
2    0.052632
3    0.052632
4    0.421053

In [11]:
def pred(st,p):
  pred=dict()
  for j in st:
    temp=[]
    date=[]
    for i in range(60,1,-1):
      # print(i)
      date.append(st[j].iloc[-i:-i+1].index.date[0])
      print('imera :',st[j].iloc[-i:-i+1].index.date[0])
      temp.append(dummy(st[j],i,p+(58-i))['prediction'].values)
      # pred[st[j].name]=temp
    #for the last day 
    date.append(st[j].iloc[-1:].index.date[0])
    print('teleutaia imera :',st[j].iloc[-1:].index.date[0])
    temp.append(dummy(st[j],1,p+57)['prediction'].values)
    pred[st[j].name]=temp
  # print(date)
  pred['date']=date
  pred_final=pd.DataFrame.from_dict(pred)
  # pred_final['Date']=date
  # pred_final.set_index('Date')
  # print(pred_final)
  return pred_final
# t=pred(st,p)

In [12]:
def create_historical(prob):
  prob=prob.rename_axis("symbol", axis="columns")
  prob=prob.T
  prob['date']=prob.columns.date[0]
  prob.columns = ['price', 'date']
  prob=prob.reset_index()
  prob=prob[['symbol','date','price']]
  return prob

In [13]:
def RPS_data(prob_final,rd):
  RPS=pd.DataFrame()

  # RPS=RPS.drop('date',axis=1)
  # print(RPS.index[2])
  for k in prob_final.index: #for everyday of a stock->index
    prob=pd.DataFrame()
    prob1=pd.DataFrame()
    predic=pd.DataFrame()
    if(prob_final['date'][k]!=prob_final['date'].tail(1).values): #if it's not for the last day 
      #for historical data of two days 
      # prob=rd.loc[(rd.index.date==prob_final['date'][k])]
      # prob1=rd.loc[ (rd.index.date==prob_final['date'][k+1])]

      mask = (rd.loc[(rd.index.date>=prob_final['date'][k])].index)
      prob_table = rd.loc[mask]
      prob = prob_table.shift(-21).head(1)
      print('prob : ',prob)
      mask1 = (rd.loc[(rd.index.date>=prob_final['date'][k+1])].index)
      prob1_table = rd.loc[mask1]
      prob1 = prob1_table.shift(-21).head(1)
      print('prob1 : ',prob1)

      prob=create_historical(prob)
      prob1=create_historical(prob1)
      hist_data=prob.append(prob1)
      print(hist_data)
      predic=prob_final.loc[prob_final['date']==prob_final['date'][k]] #find predictions of this day
      predic=predic.drop('date',axis=1)
      # print(predic)
      data=pd.DataFrame(index=predic.columns)
      data=data.reset_index()
      # print(data)
      data[['Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']]=(0,0,0,0,0)
      for i in range(len(np.array_split(predic.values[0],46))-1):
        data.loc[i,['Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']]=np.array_split(predic.values[0],46)[i][0]
      data.columns = ['ID','Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']
      # print(data)
      #now we have data->predictions and hist_data->historical data so now we can call the RPS
      rps=RPS_calculation(hist_data = hist_data , submission = data)['details']
      # print(rps) ->rps for every stock for one day 
      # print(rps['RPS'])
      tmp=pd.DataFrame(rps['RPS'].values).T
      # print(tmp.T)
      RPS=RPS.append(tmp,ignore_index=True)
      # print(RPS[RPS.index==k])

      
    else:
      #for the last day
      # prob=rd.loc[(rd.index.date==prob_final['date'][k])]
      # prob1=rd.loc[ (rd.index.date==rd.index.date[k+1])]

      # mask = (rd.loc[(rd.index.date>=prob_final['date'][k])].index)
      # prob_table = rd.loc[mask]
      # prob = prob_table.head(1)
      # print('prob teleutaio :', prob)
      # prob1 = pd.DataFrame(prob_table.iloc[1]).T
      # print('prob1 teleutaio',prob1)

      mask = (rd.loc[(rd.index.date>=prob_final['date'][k])].index)
      prob_table = rd.loc[mask]
      prob = prob_table.shift(-21).head(1)
      print('prob teleutaio :', prob)
      prob1 = pd.DataFrame(prob_table.iloc[1]).T
      print('prob1 : ',prob1)
      
      prob=create_historical(prob)
      prob1=create_historical(prob1)
      hist_data=prob.append(prob1)
      print(hist_data)
      predic=prob_final.loc[prob_final['date']==prob_final['date'][k]] #find predictions of this day
      predic=predic.drop('date',axis=1)
      # print(predic)
      data=pd.DataFrame(index=predic.columns)
      data=data.reset_index()
      # print(data)
      data[['Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']]=(0,0,0,0,0)
      for i in range(len(np.array_split(predic.values[0],46))-1):
        data.loc[i,['Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']]=np.array_split(predic.values[0],46)[i][0]
      data.columns = ['ID','Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']
      # print(data)

      #now we have data->predictions and hist_data->historical data so now we can call the RPS
      rps=RPS_calculation(hist_data = hist_data , submission = data)['details']
      # print(rps) ->rps for every stock for one day 
      # print(rps['RPS'])
      tmp=pd.DataFrame(rps['RPS'].values).T
      # print(tmp.T)
      RPS=RPS.append(tmp,ignore_index=True)              
  return RPS

In [19]:
def create_RPS(prob_final,RPS):
  d=prob_final['date']
  name=prob_final.columns[:-1]
  # print(np.split(name.values,len(name)))
  # print(d.values)
  RPS['date']=d.values
  RPS=RPS.set_index('date')
  RPS.columns=assets
  return RPS

####**For 29 May ---> 24 June**
***

#####Prepare the Dataset 

In [15]:
q2_2=rd3.copy()
q2_2=q2_2.loc[(q2_2.index<='2022-06-25') & (q2_2.index>'2021-05-01')]
q2_2

ABBV  AEP  AIZ  ALLE  AMAT  AMP  AMZN  AVB  AVY  AXP  ...  PRU  \
Date                                                              ...        
2021-06-01     2    4    1     1     4    3     4    5    1    3  ...    2   
2021-06-02     5    4    5     2     1    4     1    3    3    4  ...    3   
2021-06-03     2    2    4     4     5    4     4    1    4    3  ...    2   
2021-06-04     5    3    3     2     2    4     3    4    1    5  ...    3   
2021-06-07     1    1    4     4     1    2     5    1    4    3  ...    3   
...          ...  ...  ...   ...   ...  ...   ...  ...  ...  ...  ...  ...   
2022-06-17     5    3    2     1     5    4     3    1    1    1  ...    4   
2022-06-21     5    4    2     4     1    1     3    3    3    2  ...    1   
2022-06-22     3    5    1     3     2    2     5    5    2    1  ...    2   
2022-06-23     2    1    2     3     4    4     4    1    5    3  ...    5   
2022-06-24     4    5    3     2     3    2     1    5    4    1  ...    2   

            PYPL  RE  ROL  ROST  UNH  URI  V  VRSK  XOM  
Date                                                     
2021-06-01     5   1    4     1    2    2  5     4    4  
2021-06-02     1   3    1     1    4    1  2     2    4  
2021-06-03     5   4    3     2    1    1  4     3    3  
2021-06-04     2   2    1     4    1    1  4     1    2  
2021-06-07     4   3    4     4    3    5  3     5    5  
...          ...  ..  ...   ...  ...  ... ..   ...  ...  
2022-06-17     1   2    3     1    5    2  3     3    5  
2022-06-21     4   3    5     1    5    2  2     4    1  
2022-06-22     3   2    5     4    4    1  3     5    1  
2022-06-23     5   4    3     4    1    5  4     1    2  
2022-06-24     1   3    3     1    5    5  1     4    5  

[270 rows x 45 columns]

#####15 days
***

In [20]:
t_15d=pred(q2_2,197)
t_15d=pd.DataFrame.from_dict(t_15d)
t_15d.set_index('date')
RPS_15d= RPS_data(t_15d,rd)
RPS_15d= create_RPS(t_15d,RPS_15d)
RPS_15d
print(RPS_15d.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
2022-05-17    2
Name: UNH, dtype: int64 mikos 15
2 defaultdict(<class 'int'>, {3: 4, 1: 4, 2: 3, 4: 3, 5: 1})
imera : 2022-05-19
arxi insample Date
2022-04-28    3
Name: UNH, dtype: int64 kai telos insample Date
2022-05-17    2
2022-05-18    5
Name: UNH, dtype: int64 mikos 15
5 defaultdict(<class 'int'>, {3: 3, 1: 4, 2: 3, 4: 3, 5: 2})
imera : 2022-05-20
arxi insample Date
2022-04-29    1
Name: UNH, dtype: int64 kai telos insample Date
2022-05-18    5
2022-05-19    5
Name: UNH, dtype: int64 mikos 15
5 defaultdict(<class 'int'>, {1: 4, 2: 3, 4: 3, 5: 3, 3: 2})
imera : 2022-05-23
arxi insample Date
2022-05-02    2
Name: UNH, dtype: int64 kai telos insample Date
2022-05-19    5
2022-05-20    3
Name: UNH, dtype: int64 mikos 15
3 defaultdict(<class 'int'>, {2: 3, 1: 3, 4: 3, 5: 3, 3: 3})
imera : 2022-05-24
arxi insample Date
2022-05-03    1
Name: UNH, dtype: int64 kai telos insample Date
2022-05-20    3
2022-05-23    5
Name: UNH, dtype:

In [21]:
RPS_15d.mean(axis=1)

date
2022-03-30    0.171141
2022-03-31    0.164543
2022-04-01    0.172365
2022-04-04    0.181807
2022-04-05    0.173314
2022-04-06    0.176395
2022-04-07    0.164030
2022-04-08    0.128988
2022-04-11    0.185916
2022-04-12    0.200178
2022-04-13    0.138351
2022-04-14    0.195832
2022-04-18    0.148030
2022-04-19    0.181136
2022-04-20    0.177857
2022-04-21    0.157590
2022-04-22    0.122943
2022-04-25    0.177620
2022-04-26    0.199546
2022-04-27    0.192356
2022-04-28    0.190933
2022-04-29    0.148306
2022-05-02    0.188010
2022-05-03    0.143802
2022-05-04    0.162370
2022-05-05    0.146528
2022-05-06    0.176198
2022-05-09    0.153719
2022-05-10    0.139180
2022-05-11    0.162410
2022-05-12    0.176988
2022-05-13    0.188800
2022-05-16    0.169600
2022-05-17    0.184099
2022-05-18    0.150242
2022-05-19    0.175842
2022-05-20    0.181886
2022-05-23    0.189788
2022-05-24    0.138114
2022-05-25    0.150084
2022-05-26    0.172168
2022-05-27    0.171852
2022-05-31    0.171299
2022-0

In [22]:
RPS_15d.mean(axis=1).mean()

0.16797234567901234

#####One Month (20 working days)
***

In [25]:
t_1m=pred(q2_2,192)
t_1m=pd.DataFrame.from_dict(t_1m)
t_1m.set_index('date')
RPS_1m= RPS_data(t_1m,rd)
RPS_1m= create_RPS(t_1m,RPS_1m)
RPS_1m
print(RPS_1m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
2022-05-17    2
Name: UNH, dtype: int64 mikos 20
2 defaultdict(<class 'int'>, {2: 5, 3: 7, 1: 4, 4: 3, 5: 1})
imera : 2022-05-19
arxi insample Date
2022-04-21    2
Name: UNH, dtype: int64 kai telos insample Date
2022-05-17    2
2022-05-18    5
Name: UNH, dtype: int64 mikos 20
5 defaultdict(<class 'int'>, {2: 4, 3: 7, 1: 4, 4: 3, 5: 2})
imera : 2022-05-20
arxi insample Date
2022-04-22    3
Name: UNH, dtype: int64 kai telos insample Date
2022-05-18    5
2022-05-19    5
Name: UNH, dtype: int64 mikos 20
5 defaultdict(<class 'int'>, {3: 7, 1: 4, 2: 3, 4: 3, 5: 3})
imera : 2022-05-23
arxi insample Date
2022-04-25    3
Name: UNH, dtype: int64 kai telos insample Date
2022-05-19    5
2022-05-20    3
Name: UNH, dtype: int64 mikos 20
3 defaultdict(<class 'int'>, {3: 7, 1: 4, 2: 3, 4: 3, 5: 3})
imera : 2022-05-24
arxi insample Date
2022-04-26    3
Name: UNH, dtype: int64 kai telos insample Date
2022-05-20    3
2022-05-23    5
Name: UNH, dtype:

In [26]:
RPS_1m.mean(axis=1)

date
2022-03-30    0.172400
2022-03-31    0.162244
2022-04-01    0.164978
2022-04-04    0.180178
2022-04-05    0.172444
2022-04-06    0.174444
2022-04-07    0.159311
2022-04-08    0.145467
2022-04-11    0.175578
2022-04-12    0.174533
2022-04-13    0.139444
2022-04-14    0.179756
2022-04-18    0.149578
2022-04-19    0.181844
2022-04-20    0.170533
2022-04-21    0.157422
2022-04-22    0.130356
2022-04-25    0.182267
2022-04-26    0.189756
2022-04-27    0.194333
2022-04-28    0.190089
2022-04-29    0.149711
2022-05-02    0.193489
2022-05-03    0.132467
2022-05-04    0.166222
2022-05-05    0.147911
2022-05-06    0.172644
2022-05-09    0.153200
2022-05-10    0.154200
2022-05-11    0.161978
2022-05-12    0.177200
2022-05-13    0.180556
2022-05-16    0.160600
2022-05-17    0.180111
2022-05-18    0.148844
2022-05-19    0.170689
2022-05-20    0.184022
2022-05-23    0.180133
2022-05-24    0.140089
2022-05-25    0.157667
2022-05-26    0.182733
2022-05-27    0.169200
2022-05-31    0.170489
2022-0

In [27]:
RPS_1m.mean(axis=1).mean()

0.16685666666666668

#####Two Months 
***

In [33]:
t_2m=pred(q2_2,172)
t_2m=pd.DataFrame.from_dict(t_2m)
t_2m.set_index('date')
RPS_2m= RPS_data(t_2m,rd)
RPS_2m= create_RPS(t_2m,RPS_2m)
RPS_2m
print(RPS_2m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
2022-05-17    2
Name: UNH, dtype: int64 mikos 40
2 defaultdict(<class 'int'>, {4: 6, 5: 6, 1: 6, 2: 9, 3: 13})
imera : 2022-05-19
arxi insample Date
2022-03-23    5
Name: UNH, dtype: int64 kai telos insample Date
2022-05-17    2
2022-05-18    5
Name: UNH, dtype: int64 mikos 40
5 defaultdict(<class 'int'>, {5: 7, 1: 6, 2: 9, 3: 13, 4: 5})
imera : 2022-05-20
arxi insample Date
2022-03-24    1
Name: UNH, dtype: int64 kai telos insample Date
2022-05-18    5
2022-05-19    5
Name: UNH, dtype: int64 mikos 40
5 defaultdict(<class 'int'>, {1: 6, 2: 9, 5: 7, 3: 13, 4: 5})
imera : 2022-05-23
arxi insample Date
2022-03-25    2
Name: UNH, dtype: int64 kai telos insample Date
2022-05-19    5
2022-05-20    3
Name: UNH, dtype: int64 mikos 40
3 defaultdict(<class 'int'>, {2: 9, 1: 5, 5: 7, 3: 14, 4: 5})
imera : 2022-05-24
arxi insample Date
2022-03-28    1
Name: UNH, dtype: int64 kai telos insample Date
2022-05-20    3
2022-05-23    5
Name: UNH, dt

In [34]:
RPS_2m.mean(axis=1).mean()

0.1614289814814815

In [35]:
RPS_2m.mean(axis=1)

date
2022-03-30    0.168900
2022-03-31    0.153672
2022-04-01    0.168411
2022-04-04    0.150511
2022-04-05    0.152678
2022-04-06    0.160306
2022-04-07    0.160389
2022-04-08    0.139417
2022-04-11    0.174261
2022-04-12    0.174750
2022-04-13    0.146022
2022-04-14    0.173650
2022-04-18    0.153806
2022-04-19    0.173800
2022-04-20    0.169800
2022-04-21    0.154400
2022-04-22    0.140456
2022-04-25    0.170572
2022-04-26    0.171556
2022-04-27    0.168761
2022-04-28    0.171483
2022-04-29    0.154333
2022-05-02    0.173461
2022-05-03    0.140161
2022-05-04    0.157833
2022-05-05    0.146939
2022-05-06    0.165378
2022-05-09    0.154333
2022-05-10    0.149367
2022-05-11    0.152178
2022-05-12    0.172206
2022-05-13    0.173983
2022-05-16    0.145128
2022-05-17    0.172117
2022-05-18    0.153356
2022-05-19    0.158244
2022-05-20    0.163011
2022-05-23    0.182539
2022-05-24    0.138494
2022-05-25    0.147550
2022-05-26    0.168711
2022-05-27    0.159950
2022-05-31    0.162406
2022-0

#####Three Months 
***

In [40]:
t_3m=pred(q2_2,152)
t_3m=pd.DataFrame.from_dict(t_3m)
t_3m.set_index('date')
RPS_3m= RPS_data(t_3m,rd)
RPS_3m= create_RPS(t_3m,RPS_3m)
RPS_3m
print(RPS_3m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
2022-05-17    2
Name: UNH, dtype: int64 mikos 60
2 defaultdict(<class 'int'>, {5: 11, 2: 11, 4: 11, 3: 17, 1: 10})
imera : 2022-05-19
arxi insample Date
2022-02-23    2
Name: UNH, dtype: int64 kai telos insample Date
2022-05-17    2
2022-05-18    5
Name: UNH, dtype: int64 mikos 60
5 defaultdict(<class 'int'>, {2: 11, 5: 11, 4: 11, 3: 17, 1: 10})
imera : 2022-05-20
arxi insample Date
2022-02-24    5
Name: UNH, dtype: int64 kai telos insample Date
2022-05-18    5
2022-05-19    5
Name: UNH, dtype: int64 mikos 60
5 defaultdict(<class 'int'>, {5: 12, 4: 11, 3: 17, 1: 10, 2: 10})
imera : 2022-05-23
arxi insample Date
2022-02-25    4
Name: UNH, dtype: int64 kai telos insample Date
2022-05-19    5
2022-05-20    3
Name: UNH, dtype: int64 mikos 60
3 defaultdict(<class 'int'>, {4: 11, 5: 11, 3: 18, 1: 10, 2: 10})
imera : 2022-05-24
arxi insample Date
2022-02-28    5
Name: UNH, dtype: int64 kai telos insample Date
2022-05-20    3
2022-05-23   

In [42]:
RPS_3m.mean(axis=1).mean()

0.15955983539094648

In [43]:
RPS_3m.mean(axis=1)

date
2022-03-30    0.169244
2022-03-31    0.148136
2022-04-01    0.164109
2022-04-04    0.144467
2022-04-05    0.149477
2022-04-06    0.161793
2022-04-07    0.157496
2022-04-08    0.140491
2022-04-11    0.172294
2022-04-12    0.171402
2022-04-13    0.148914
2022-04-14    0.165198
2022-04-18    0.153435
2022-04-19    0.173040
2022-04-20    0.168832
2022-04-21    0.152674
2022-04-22    0.144435
2022-04-25    0.164173
2022-04-26    0.167430
2022-04-27    0.171511
2022-04-28    0.171756
2022-04-29    0.154556
2022-05-02    0.175284
2022-05-03    0.136526
2022-05-04    0.159294
2022-05-05    0.145496
2022-05-06    0.165430
2022-05-09    0.151909
2022-05-10    0.145291
2022-05-11    0.150822
2022-05-12    0.169504
2022-05-13    0.172644
2022-05-16    0.147432
2022-05-17    0.170133
2022-05-18    0.151548
2022-05-19    0.158469
2022-05-20    0.163741
2022-05-23    0.173817
2022-05-24    0.141943
2022-05-25    0.150412
2022-05-26    0.162304
2022-05-27    0.154765
2022-05-31    0.161884
2022-0

#####Six Months
***

In [45]:
t_6m=pred(q2_2,92)
t_6m=pd.DataFrame.from_dict(t_6m)
t_6m.set_index('date')
RPS_6m= RPS_data(t_6m,rd)
RPS_6m= create_RPS(t_6m,RPS_6m)
RPS_6m
print(RPS_6m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
arxi insample Date
2021-10-13    5
Name: URI, dtype: int64 kai telos insample Date
2022-04-01    1
2022-04-04    1
Name: URI, dtype: int64 mikos 120
--------------------------------------------------------------- False
1 defaultdict(<class 'int'>, {5: 27, 1: 35, 3: 17, 4: 21, 2: 20})
imera : 2022-04-06
arxi insample Date
2021-10-14    1
Name: URI, dtype: int64 kai telos insample Date
2022-04-04    1
2022-04-05    1
Name: URI, dtype: int64 mikos 120
--------------------------------------------------------------- False
1 defaultdict(<class 'int'>, {1: 36, 3: 17, 5: 26, 4: 21, 2: 20})
imera : 2022-04-07
arxi insample Date
2021-10-15    3
Name: URI, dtype: int64 kai telos insample Date
2022-04-05    1
2022-04-06    1
Name: URI, dtype: int64 mikos 120
--------------------------------------------------------------- False
1 defaultdict(<class 'int'>, {3: 17, 5: 26, 4: 21, 1: 36, 2: 20})
imera : 2022-04-08
arxi insample Date
2021-10-18    

In [46]:
RPS_6m.mean(axis=1).mean()

0.15896523662551443

In [47]:
RPS_6m.mean(axis=1)

date
2022-03-30    0.167005
2022-03-31    0.153109
2022-04-01    0.163518
2022-04-04    0.148928
2022-04-05    0.149662
2022-04-06    0.159019
2022-04-07    0.156232
2022-04-08    0.141451
2022-04-11    0.167114
2022-04-12    0.166108
2022-04-13    0.144973
2022-04-14    0.167908
2022-04-18    0.155764
2022-04-19    0.171442
2022-04-20    0.163228
2022-04-21    0.153421
2022-04-22    0.144474
2022-04-25    0.164704
2022-04-26    0.169196
2022-04-27    0.166888
2022-04-28    0.169233
2022-04-29    0.153737
2022-05-02    0.172893
2022-05-03    0.143109
2022-05-04    0.162569
2022-05-05    0.147201
2022-05-06    0.163504
2022-05-09    0.154846
2022-05-10    0.142985
2022-05-11    0.150370
2022-05-12    0.165560
2022-05-13    0.171317
2022-05-16    0.146475
2022-05-17    0.166694
2022-05-18    0.148856
2022-05-19    0.159296
2022-05-20    0.164504
2022-05-23    0.172406
2022-05-24    0.145376
2022-05-25    0.147252
2022-05-26    0.162141
2022-05-27    0.154306
2022-05-31    0.161248
2022-0

#####All the samples 
***

In [48]:
#Αυτή η συνάρτηση παίρνει τα data και κάνει τη dummy μέτρηση για το διάστημα ενός χρόνου (όσο οριστεί στην ουσία το insample) για μια μετοχή
n=dict() 
def dummy2(st,i):
  flag=False
  insample=st.iloc[:-i]
  print('arxi',insample.head(1),'kai telos ',insample.tail(1),'mikos',len(insample))
  # if(len(insample)!=253):
  #   print('---------------------------------------------------------------',flag)
  count=defaultdict(int)
  for word in insample.values:
    count[word]+=1
  print(word,count)
  count=sorted(count.items()) #list Η πρώτη τιμή είναι η κλάση και η δεύτερη πόσες φορές είδα τον αριθμό.
  temp=[]
  for k in range(5):
    flag=True
    for l in count:
      if(l[0]==k+1):
        temp.append(l[1]/len(insample))
        flag=False
        break
    if(flag):
      temp.append(0)
  # print(temp,count)
  data={
      'prediction':temp
  }
  forecast=pd.DataFrame(data)
  return forecast
# #για όλες τις μετοχές υπολογίζεται το counter τους
dummy2(rd3['ABBV'],60)


arxi Date
2021-06-01    2
Name: ABBV, dtype: int64 kai telos  Date
2022-06-21    5
Name: ABBV, dtype: int64 mikos 267
5 defaultdict(<class 'int'>, {2: 51, 5: 67, 1: 41, 3: 49, 4: 59})


prediction
0    0.153558
1    0.191011
2    0.183521
3    0.220974
4    0.250936

In [49]:
def pred2(st):
  pred=dict()
  for j in st:
    temp=[]
    date=[]
    for i in range(59,1,-1):
      # print(i)
      date.append(q2_2[j].iloc[-i:-i+1].index.date[0])
      print(date)
      temp.append(dummy2(q2_2[j],i)['prediction'].values)
      # pred[q2_2[j].name]=temp
    #for the last day 
    date.append(q2_2[j].iloc[-1:].index.date[0])
    temp.append(dummy2(q2_2[j],1)['prediction'].values)
    pred[q2_2[j].name]=temp
  # print(date)
  pred['date']=date
  pred_final=pd.DataFrame.from_dict(pred)
  # pred_final['Date']=date
  # pred_final.set_index('Date')
  # print(pred_final)
  return pred_final


In [50]:
t_all=pred2(q2_2)
t_all=pd.DataFrame.from_dict(t_all)
t_all.set_index('date')
RPS_all= RPS_data(t_all,rd)
RPS_all= create_RPS(t_all,RPS_all)
RPS_all
print(RPS_all.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
[datetime.date(2022, 3, 31), datetime.date(2022, 4, 1), datetime.date(2022, 4, 4), datetime.date(2022, 4, 5), datetime.date(2022, 4, 6), datetime.date(2022, 4, 7), datetime.date(2022, 4, 8), datetime.date(2022, 4, 11), datetime.date(2022, 4, 12), datetime.date(2022, 4, 13), datetime.date(2022, 4, 14), datetime.date(2022, 4, 18), datetime.date(2022, 4, 19), datetime.date(2022, 4, 20), datetime.date(2022, 4, 21), datetime.date(2022, 4, 22), datetime.date(2022, 4, 25), datetime.date(2022, 4, 26), datetime.date(2022, 4, 27), datetime.date(2022, 4, 28), datetime.date(2022, 4, 29), datetime.date(2022, 5, 2), datetime.date(2022, 5, 3), datetime.date(2022, 5, 4), datetime.date(2022, 5, 5), datetime.date(2022, 5, 6), datetime.date(2022, 5, 9), datetime.date(2022, 5, 10), datetime.date(2022, 5, 11), datetime.date(2022, 5, 12), datetime.date(2022, 5, 13), datetime.date(2022, 5, 16), datetime.date(2022, 5, 17), datetime.date(2022, 5, 18), date

In [51]:
RPS_all.mean(axis=1)

date
2022-03-31    0.155759
2022-04-01    0.161060
2022-04-04    0.154158
2022-04-05    0.152814
2022-04-06    0.158956
2022-04-07    0.157178
2022-04-08    0.148865
2022-04-11    0.163936
2022-04-12    0.159926
2022-04-13    0.152319
2022-04-14    0.161194
2022-04-18    0.159729
2022-04-19    0.166285
2022-04-20    0.163571
2022-04-21    0.153143
2022-04-22    0.153606
2022-04-25    0.160884
2022-04-26    0.160833
2022-04-27    0.160151
2022-04-28    0.162827
2022-04-29    0.159233
2022-05-02    0.163745
2022-05-03    0.150514
2022-05-04    0.161379
2022-05-05    0.151461
2022-05-06    0.163969
2022-05-09    0.156239
2022-05-10    0.150216
2022-05-11    0.151428
2022-05-12    0.163562
2022-05-13    0.163951
2022-05-16    0.152224
2022-05-17    0.163042
2022-05-18    0.151596
2022-05-19    0.156430
2022-05-20    0.160660
2022-05-23    0.163995
2022-05-24    0.152937
2022-05-25    0.155071
2022-05-26    0.157578
2022-05-27    0.154788
2022-05-31    0.161678
2022-06-01    0.164311
2022-0

In [52]:
RPS_all.mean(axis=1).mean()

0.15825576318227455

####**For 26 June ---> 22 July**
***

#####Prepare the Dataset 
***

In [53]:
q2_2=rd3.copy()
q2_2=q2_2.loc[(q2_2.index<='2022-07-23') & (q2_2.index>'2021-06-01')]
q2_2

ABBV  AEP  AIZ  ALLE  AMAT  AMP  AMZN  AVB  AVY  AXP  ...  PRU  \
Date                                                              ...        
2021-06-02     5    4    5     2     1    4     1    3    3    4  ...    3   
2021-06-03     2    2    4     4     5    4     4    1    4    3  ...    2   
2021-06-04     5    3    3     2     2    4     3    4    1    5  ...    3   
2021-06-07     1    1    4     4     1    2     5    1    4    3  ...    3   
2021-06-08     5    5    2     2     2    1     5    3    3    1  ...    1   
...          ...  ...  ...   ...   ...  ...   ...  ...  ...  ...  ...  ...   
2022-07-18     1    1    2     5     5    3     4    2    4    4  ...    3   
2022-07-19     1    1    3     4     5    5     5    2    4    4  ...    4   
2022-07-20     1    2    2     5     5    4     4    3    4    3  ...    2   
2022-07-21     4    5    4     3     1    3     1    5    3    5  ...    2   
2022-07-22     4    5    5     2     2    3     1    2    2    4  ...    5   

            PYPL  RE  ROL  ROST  UNH  URI  V  VRSK  XOM  
Date                                                     
2021-06-02     1   3    1     1    4    1  2     2    4  
2021-06-03     5   4    3     2    1    1  4     3    3  
2021-06-04     2   2    1     4    1    1  4     1    2  
2021-06-07     4   3    4     4    3    5  3     5    5  
2021-06-08     4   2    3     3    3    1  4     4    5  
...          ...  ..  ...   ...  ...  ... ..   ...  ...  
2022-07-18     5   3    4     3    3    5  3     3    2  
2022-07-19     5   2    2     5    1    5  2     4    4  
2022-07-20     5   2    3     4    3    4  4     4    1  
2022-07-21     1   5    3     3    3    1  2     3    2  
2022-07-22     4   4    3     1    5    4  3     1    5  

[288 rows x 45 columns]

#####15 days
***

In [57]:
t_15d=pred(q2_2,215)
t_15d=pd.DataFrame.from_dict(t_15d)
t_15d.set_index('date')
RPS_15d= RPS_data(t_15d,rd)
RPS_15d= create_RPS(t_15d,RPS_15d)
RPS_15d
print(RPS_15d.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
2022-06-14    2
Name: UNH, dtype: int64 mikos 15
2 defaultdict(<class 'int'>, {2: 5, 1: 3, 3: 1, 4: 5, 5: 1})
imera : 2022-06-16
arxi insample Date
2022-05-25    2
Name: UNH, dtype: int64 kai telos insample Date
2022-06-14    2
2022-06-15    5
Name: UNH, dtype: int64 mikos 15
5 defaultdict(<class 'int'>, {2: 4, 1: 3, 3: 1, 4: 5, 5: 2})
imera : 2022-06-17
arxi insample Date
2022-05-26    1
Name: UNH, dtype: int64 kai telos insample Date
2022-06-15    5
2022-06-16    1
Name: UNH, dtype: int64 mikos 15
1 defaultdict(<class 'int'>, {1: 4, 3: 1, 2: 3, 4: 5, 5: 2})
imera : 2022-06-21
arxi insample Date
2022-05-27    1
Name: UNH, dtype: int64 kai telos insample Date
2022-06-16    1
2022-06-17    5
Name: UNH, dtype: int64 mikos 15
5 defaultdict(<class 'int'>, {1: 3, 3: 1, 2: 3, 4: 5, 5: 3})
imera : 2022-06-22
arxi insample Date
2022-05-31    3
Name: UNH, dtype: int64 kai telos insample Date
2022-06-17    5
2022-06-21    5
Name: UNH, dtype:

In [58]:
RPS_15d.mean(axis=1)

date
2022-04-27    0.192356
2022-04-28    0.190933
2022-04-29    0.148306
2022-05-02    0.188010
2022-05-03    0.143802
2022-05-04    0.162370
2022-05-05    0.146528
2022-05-06    0.176198
2022-05-09    0.153719
2022-05-10    0.139180
2022-05-11    0.162410
2022-05-12    0.176988
2022-05-13    0.188800
2022-05-16    0.169600
2022-05-17    0.184099
2022-05-18    0.150242
2022-05-19    0.175842
2022-05-20    0.181886
2022-05-23    0.189788
2022-05-24    0.138114
2022-05-25    0.150084
2022-05-26    0.172168
2022-05-27    0.171852
2022-05-31    0.171299
2022-06-01    0.170035
2022-06-02    0.183111
2022-06-03    0.141156
2022-06-06    0.160790
2022-06-07    0.178252
2022-06-08    0.176909
2022-06-09    0.153007
2022-06-10    0.161778
2022-06-13    0.189274
2022-06-14    0.167032
2022-06-15    0.152178
2022-06-16    0.168889
2022-06-17    0.184415
2022-06-21    0.164622
2022-06-22    0.176514
2022-06-23    0.146133
2022-06-24    0.188168
2022-06-27    0.177857
2022-06-28    0.198123
2022-0

In [59]:
RPS_15d.mean(axis=1).mean()

0.17049086419753087

#####One Month(20 working days)
***

In [61]:
t_1m=pred(q2_2,210)
t_1m=pd.DataFrame.from_dict(t_1m)
t_1m.set_index('date')
RPS_1m= RPS_data(t_1m,rd)
RPS_1m= create_RPS(t_1m,RPS_1m)
RPS_1m
print(RPS_1m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
arxi insample Date
2022-04-04    1
Name: URI, dtype: int64 kai telos insample Date
2022-04-29    1
2022-05-02    5
Name: URI, dtype: int64 mikos 20
--------------------------------------------------------------- False
5 defaultdict(<class 'int'>, {1: 7, 4: 2, 5: 8, 2: 3})
imera : 2022-05-04
arxi insample Date
2022-04-05    1
Name: URI, dtype: int64 kai telos insample Date
2022-05-02    5
2022-05-03    3
Name: URI, dtype: int64 mikos 20
--------------------------------------------------------------- False
3 defaultdict(<class 'int'>, {1: 6, 4: 2, 5: 8, 2: 3, 3: 1})
imera : 2022-05-05
arxi insample Date
2022-04-06    1
Name: URI, dtype: int64 kai telos insample Date
2022-05-03    3
2022-05-04    1
Name: URI, dtype: int64 mikos 20
--------------------------------------------------------------- False
1 defaultdict(<class 'int'>, {1: 6, 4: 2, 5: 8, 2: 3, 3: 1})
imera : 2022-05-06
arxi insample Date
2022-04-07    1
Name: URI, dtype: int6

In [62]:
RPS_1m.mean(axis=1).mean()

0.16855777777777778

In [63]:
RPS_1m.mean(axis=1)

date
2022-04-27    0.194333
2022-04-28    0.190089
2022-04-29    0.149711
2022-05-02    0.193489
2022-05-03    0.132467
2022-05-04    0.166222
2022-05-05    0.147911
2022-05-06    0.172644
2022-05-09    0.153200
2022-05-10    0.154200
2022-05-11    0.161978
2022-05-12    0.177200
2022-05-13    0.180556
2022-05-16    0.160600
2022-05-17    0.180111
2022-05-18    0.148844
2022-05-19    0.170689
2022-05-20    0.184022
2022-05-23    0.180133
2022-05-24    0.140089
2022-05-25    0.157667
2022-05-26    0.182733
2022-05-27    0.169200
2022-05-31    0.170489
2022-06-01    0.182822
2022-06-02    0.169200
2022-06-03    0.152244
2022-06-06    0.156778
2022-06-07    0.171711
2022-06-08    0.171644
2022-06-09    0.152578
2022-06-10    0.163756
2022-06-13    0.175133
2022-06-14    0.159467
2022-06-15    0.166000
2022-06-16    0.166533
2022-06-17    0.176911
2022-06-21    0.166378
2022-06-22    0.174111
2022-06-23    0.159067
2022-06-24    0.162400
2022-06-27    0.174467
2022-06-28    0.178844
2022-0

#####Two Months 
***

In [64]:
t_2m=pred(q2_2,190)
t_2m=pd.DataFrame.from_dict(t_2m)
t_2m.set_index('date')
RPS_2m= RPS_data(t_2m,rd)
RPS_2m= create_RPS(t_2m,RPS_2m)
RPS_2m
print(RPS_2m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
arxi insample Date
2022-03-07    5
Name: URI, dtype: int64 kai telos insample Date
2022-04-29    1
2022-05-02    5
Name: URI, dtype: int64 mikos 40
--------------------------------------------------------------- False
5 defaultdict(<class 'int'>, {5: 13, 3: 2, 2: 8, 4: 8, 1: 9})
imera : 2022-05-04
arxi insample Date
2022-03-08    3
Name: URI, dtype: int64 kai telos insample Date
2022-05-02    5
2022-05-03    3
Name: URI, dtype: int64 mikos 40
--------------------------------------------------------------- False
3 defaultdict(<class 'int'>, {3: 3, 5: 12, 2: 8, 4: 8, 1: 9})
imera : 2022-05-05
arxi insample Date
2022-03-09    5
Name: URI, dtype: int64 kai telos insample Date
2022-05-03    3
2022-05-04    1
Name: URI, dtype: int64 mikos 40
--------------------------------------------------------------- False
1 defaultdict(<class 'int'>, {5: 12, 2: 8, 4: 8, 1: 10, 3: 2})
imera : 2022-05-06
arxi insample Date
2022-03-10    5
Name: URI, d

In [65]:
RPS_2m.mean(axis=1).mean()

0.16302546296296297

In [66]:
RPS_2m.mean(axis=1)

date
2022-04-27    0.168761
2022-04-28    0.171483
2022-04-29    0.154333
2022-05-02    0.173461
2022-05-03    0.140161
2022-05-04    0.157833
2022-05-05    0.146939
2022-05-06    0.165378
2022-05-09    0.154333
2022-05-10    0.149367
2022-05-11    0.152178
2022-05-12    0.172206
2022-05-13    0.173983
2022-05-16    0.145128
2022-05-17    0.172117
2022-05-18    0.153356
2022-05-19    0.158244
2022-05-20    0.163011
2022-05-23    0.182539
2022-05-24    0.138494
2022-05-25    0.147550
2022-05-26    0.168711
2022-05-27    0.159950
2022-05-31    0.162406
2022-06-01    0.181317
2022-06-02    0.167817
2022-06-03    0.153767
2022-06-06    0.156939
2022-06-07    0.157439
2022-06-08    0.167700
2022-06-09    0.159822
2022-06-10    0.163200
2022-06-13    0.176428
2022-06-14    0.163639
2022-06-15    0.166072
2022-06-16    0.168844
2022-06-17    0.176511
2022-06-21    0.163172
2022-06-22    0.159728
2022-06-23    0.153867
2022-06-24    0.161978
2022-06-27    0.173783
2022-06-28    0.170039
2022-0

#####Three Months 
***

In [67]:
t_3m=pred(q2_2,170)
t_3m=pd.DataFrame.from_dict(t_3m)
t_3m.set_index('date')
RPS_3m= RPS_data(t_3m,rd)
RPS_3m= create_RPS(t_3m,RPS_3m)
RPS_3m
print(RPS_3m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
arxi insample Date
2022-02-04    5
Name: URI, dtype: int64 kai telos insample Date
2022-04-29    1
2022-05-02    5
Name: URI, dtype: int64 mikos 60
--------------------------------------------------------------- False
5 defaultdict(<class 'int'>, {5: 20, 1: 15, 4: 12, 2: 10, 3: 3})
imera : 2022-05-04
arxi insample Date
2022-02-07    5
Name: URI, dtype: int64 kai telos insample Date
2022-05-02    5
2022-05-03    3
Name: URI, dtype: int64 mikos 60
--------------------------------------------------------------- False
3 defaultdict(<class 'int'>, {5: 19, 1: 15, 4: 12, 2: 10, 3: 4})
imera : 2022-05-05
arxi insample Date
2022-02-08    5
Name: URI, dtype: int64 kai telos insample Date
2022-05-03    3
2022-05-04    1
Name: URI, dtype: int64 mikos 60
--------------------------------------------------------------- False
1 defaultdict(<class 'int'>, {5: 18, 1: 16, 4: 12, 2: 10, 3: 4})
imera : 2022-05-06
arxi insample Date
2022-02-09    1
Name

In [68]:
RPS_3m.mean(axis=1).mean()

0.1608428395061728

In [69]:
RPS_3m.mean(axis=1)

date
2022-04-27    0.171511
2022-04-28    0.171756
2022-04-29    0.154556
2022-05-02    0.175284
2022-05-03    0.136526
2022-05-04    0.159294
2022-05-05    0.145496
2022-05-06    0.165430
2022-05-09    0.151909
2022-05-10    0.145291
2022-05-11    0.150822
2022-05-12    0.169504
2022-05-13    0.172644
2022-05-16    0.147432
2022-05-17    0.170133
2022-05-18    0.151548
2022-05-19    0.158469
2022-05-20    0.163741
2022-05-23    0.173817
2022-05-24    0.141943
2022-05-25    0.150412
2022-05-26    0.162304
2022-05-27    0.154765
2022-05-31    0.161884
2022-06-01    0.168047
2022-06-02    0.159284
2022-06-03    0.159812
2022-06-06    0.152612
2022-06-07    0.151462
2022-06-08    0.163321
2022-06-09    0.155222
2022-06-10    0.161281
2022-06-13    0.176323
2022-06-14    0.165259
2022-06-15    0.171440
2022-06-16    0.174575
2022-06-17    0.175760
2022-06-21    0.149049
2022-06-22    0.156891
2022-06-23    0.147491
2022-06-24    0.171583
2022-06-27    0.165993
2022-06-28    0.167286
2022-0

#####Six Months 
***

In [70]:
t_6m=pred(q2_2,110)
t_6m=pd.DataFrame.from_dict(t_6m)
t_6m.set_index('date')
RPS_6m= RPS_data(t_6m,rd)
RPS_6m= create_RPS(t_6m,RPS_6m)
RPS_6m
print(RPS_6m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
arxi insample Date
2021-11-09    1
Name: URI, dtype: int64 kai telos insample Date
2022-04-29    1
2022-05-02    5
Name: URI, dtype: int64 mikos 120
--------------------------------------------------------------- False
5 defaultdict(<class 'int'>, {1: 36, 4: 17, 2: 22, 3: 14, 5: 31})
imera : 2022-05-04
arxi insample Date
2021-11-10    4
Name: URI, dtype: int64 kai telos insample Date
2022-05-02    5
2022-05-03    3
Name: URI, dtype: int64 mikos 120
--------------------------------------------------------------- False
3 defaultdict(<class 'int'>, {4: 17, 2: 22, 3: 15, 1: 35, 5: 31})
imera : 2022-05-05
arxi insample Date
2021-11-11    2
Name: URI, dtype: int64 kai telos insample Date
2022-05-03    3
2022-05-04    1
Name: URI, dtype: int64 mikos 120
--------------------------------------------------------------- False
1 defaultdict(<class 'int'>, {2: 22, 3: 15, 1: 36, 4: 16, 5: 31})
imera : 2022-05-06
arxi insample Date
2021-11-12    

In [71]:
RPS_6m.mean(axis=1).mean()

0.1598559773662551

In [72]:
RPS_6m.mean(axis=1)

date
2022-04-27    0.166888
2022-04-28    0.169233
2022-04-29    0.153737
2022-05-02    0.172893
2022-05-03    0.143109
2022-05-04    0.162569
2022-05-05    0.147201
2022-05-06    0.163504
2022-05-09    0.154846
2022-05-10    0.142985
2022-05-11    0.150370
2022-05-12    0.165560
2022-05-13    0.171317
2022-05-16    0.146475
2022-05-17    0.166694
2022-05-18    0.148856
2022-05-19    0.159296
2022-05-20    0.164504
2022-05-23    0.172406
2022-05-24    0.145376
2022-05-25    0.147252
2022-05-26    0.162141
2022-05-27    0.154306
2022-05-31    0.161248
2022-06-01    0.177106
2022-06-02    0.159187
2022-06-03    0.162257
2022-06-06    0.152598
2022-06-07    0.150276
2022-06-08    0.162020
2022-06-09    0.158787
2022-06-10    0.166070
2022-06-13    0.168449
2022-06-14    0.160768
2022-06-15    0.168827
2022-06-16    0.169310
2022-06-17    0.176425
2022-06-21    0.149205
2022-06-22    0.147635
2022-06-23    0.149723
2022-06-24    0.168436
2022-06-27    0.167170
2022-06-28    0.161630
2022-0

#####All the samples 
***

In [73]:
t_all=pred2(q2_2)
t_all=pd.DataFrame.from_dict(t_all)
t_all.set_index('date')
RPS_all= RPS_data(t_all,rd)
RPS_all= create_RPS(t_all,RPS_all)
RPS_all
print(RPS_all.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
[datetime.date(2022, 4, 28), datetime.date(2022, 4, 29), datetime.date(2022, 5, 2), datetime.date(2022, 5, 3), datetime.date(2022, 5, 4), datetime.date(2022, 5, 5), datetime.date(2022, 5, 6), datetime.date(2022, 5, 9), datetime.date(2022, 5, 10), datetime.date(2022, 5, 11), datetime.date(2022, 5, 12), datetime.date(2022, 5, 13), datetime.date(2022, 5, 16), datetime.date(2022, 5, 17), datetime.date(2022, 5, 18), datetime.date(2022, 5, 19), datetime.date(2022, 5, 20), datetime.date(2022, 5, 23), datetime.date(2022, 5, 24), datetime.date(2022, 5, 25), datetime.date(2022, 5, 26), datetime.date(2022, 5, 27), datetime.date(2022, 5, 31), datetime.date(2022, 6, 1), datetime.date(2022, 6, 2), datetime.date(2022, 6, 3), datetime.date(2022, 6, 6), datetime.date(2022, 6, 7), datetime.date(2022, 6, 8), datetime.date(2022, 6, 9), datetime.date(2022, 6, 10), datetime.date(2022, 6, 13), datetime.date(2022, 6, 14), datetime.date(2022, 6, 15), datet

In [74]:
RPS_all.mean(axis=1).mean()

0.15855147543898884

In [75]:
RPS_all.mean(axis=1)

date
2022-04-28    0.163042
2022-04-29    0.159200
2022-05-02    0.163924
2022-05-03    0.150443
2022-05-04    0.161127
2022-05-05    0.151434
2022-05-06    0.163844
2022-05-09    0.156121
2022-05-10    0.150148
2022-05-11    0.151291
2022-05-12    0.163662
2022-05-13    0.164311
2022-05-16    0.152166
2022-05-17    0.163138
2022-05-18    0.151682
2022-05-19    0.156316
2022-05-20    0.160672
2022-05-23    0.164021
2022-05-24    0.152882
2022-05-25    0.154846
2022-05-26    0.157435
2022-05-27    0.154563
2022-05-31    0.161764
2022-06-01    0.164337
2022-06-02    0.155977
2022-06-03    0.160165
2022-06-06    0.153609
2022-06-07    0.153740
2022-06-08    0.160224
2022-06-09    0.158550
2022-06-10    0.160514
2022-06-13    0.164548
2022-06-14    0.161658
2022-06-15    0.161875
2022-06-16    0.162033
2022-06-17    0.165684
2022-06-21    0.152616
2022-06-22    0.153896
2022-06-23    0.153386
2022-06-24    0.162350
2022-06-27    0.162699
2022-06-28    0.160894
2022-06-29    0.163563
2022-0

#### **For 24 July ---> 19 August**
***

#####Prepare the Dataset 
***

In [79]:
q2_2=rd3.copy()
q2_2=q2_2.loc[(q2_2.index<='2022-08-17') & (q2_2.index>'2021-07-01')]
q2_2

ABBV  AEP  AIZ  ALLE  AMAT  AMP  AMZN  AVB  AVY  AXP  ...  PRU  \
Date                                                              ...        
2021-07-02     5    4    4     2     2    2     5    5    1    5  ...    1   
2021-07-06     4    2    1     4     1    3     3    4    5    3  ...    2   
2021-07-07     4    4    2     1     2    1     5    5    3    1  ...    1   
2021-07-08     1    1    4     2     4    5     1    4    3    5  ...    5   
2021-07-09     4    3    3     2     5    4     2    5    3    4  ...    4   
...          ...  ...  ...   ...   ...  ...   ...  ...  ...  ...  ...  ...   
2022-08-11     1    5    3     5     5    4     4    2    3    3  ...    4   
2022-08-12     2    4    4     4     1    1     2    3    1    2  ...    1   
2022-08-15     2    2    5     5     1    4     4    3    5    2  ...    3   
2022-08-16     3    4    5     4     1    4     1    5    2    2  ...    3   
2022-08-17     2    2    2     4     5    5     3    1    1    4  ...    4   

            PYPL  RE  ROL  ROST  UNH  URI  V  VRSK  XOM  
Date                                                     
2021-07-02     5   2    5     4    4    1  4     4    1  
2021-07-06     5   4    5     1    2    2  2     5    1  
2021-07-07     3   1    2     1    4    1  2     4    4  
2021-07-08     4   4    3     5    2    5  2     1    4  
2021-07-09     4   3    2     1    4    5  2     1    2  
...          ...  ..  ...   ...  ...  ... ..   ...  ...  
2022-08-11     3   2    1     4    4    2  1     1    1  
2022-08-12     4   2    2     2    3    3  5     5    1  
2022-08-15     4   4    5     5    3    3  3     1    1  
2022-08-16     1   5    2     4    4    1  2     3    5  
2022-08-17     4   5    3     1    2    1  3     3    5  

[284 rows x 45 columns]

#####15 days 
***

In [81]:
t_15d=pred(q2_2,211)
t_15d=pd.DataFrame.from_dict(t_15d)
t_15d.set_index('date')
RPS_15d= RPS_data(t_15d,rd)
RPS_15d= create_RPS(t_15d,RPS_15d)
RPS_15d
print(RPS_15d.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
2022-07-12    1
Name: UNH, dtype: int64 mikos 15
1 defaultdict(<class 'int'>, {5: 6, 4: 1, 1: 4, 3: 3, 2: 1})
imera : 2022-07-14
arxi insample Date
2022-06-22    4
Name: UNH, dtype: int64 kai telos insample Date
2022-07-12    1
2022-07-13    4
Name: UNH, dtype: int64 mikos 15
4 defaultdict(<class 'int'>, {4: 2, 1: 4, 5: 5, 3: 3, 2: 1})
imera : 2022-07-15
arxi insample Date
2022-06-23    1
Name: UNH, dtype: int64 kai telos insample Date
2022-07-13    4
2022-07-14    5
Name: UNH, dtype: int64 mikos 15
5 defaultdict(<class 'int'>, {1: 4, 5: 6, 3: 3, 2: 1, 4: 1})
imera : 2022-07-18
arxi insample Date
2022-06-24    5
Name: UNH, dtype: int64 kai telos insample Date
2022-07-14    5
2022-07-15    1
Name: UNH, dtype: int64 mikos 15
1 defaultdict(<class 'int'>, {5: 6, 3: 3, 2: 1, 1: 4, 4: 1})
imera : 2022-07-19
arxi insample Date
2022-06-27    5
Name: UNH, dtype: int64 kai telos insample Date
2022-07-15    1
2022-07-18    3
Name: UNH, dtype:

In [82]:
RPS_15d.mean(axis=1).mean()

0.17064559670781895

In [83]:
RPS_15d.mean(axis=1)

date
2022-05-23    0.189788
2022-05-24    0.138114
2022-05-25    0.150084
2022-05-26    0.172168
2022-05-27    0.171852
2022-05-31    0.171299
2022-06-01    0.170035
2022-06-02    0.183111
2022-06-03    0.141156
2022-06-06    0.160790
2022-06-07    0.178252
2022-06-08    0.176909
2022-06-09    0.153007
2022-06-10    0.161778
2022-06-13    0.189274
2022-06-14    0.167032
2022-06-15    0.152178
2022-06-16    0.168889
2022-06-17    0.184415
2022-06-21    0.164622
2022-06-22    0.176514
2022-06-23    0.146133
2022-06-24    0.188168
2022-06-27    0.177857
2022-06-28    0.198123
2022-06-29    0.174854
2022-06-30    0.161580
2022-07-01    0.184533
2022-07-05    0.163002
2022-07-06    0.177857
2022-07-07    0.184652
2022-07-08    0.160790
2022-07-11    0.190341
2022-07-12    0.189788
2022-07-13    0.171101
2022-07-14    0.156444
2022-07-15    0.170351
2022-07-18    0.160790
2022-07-19    0.175763
2022-07-20    0.182479
2022-07-21    0.184099
2022-07-22    0.156879
2022-07-25    0.172089
2022-0

#####One Month 
***

In [85]:
t_1m=pred(q2_2,206)
t_1m=pd.DataFrame.from_dict(t_1m)
t_1m.set_index('date')
RPS_1m= RPS_data(t_1m,rd)
RPS_1m= create_RPS(t_1m,RPS_1m)
RPS_1m
print(RPS_1m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
arxi insample Date
2022-04-29    1
Name: URI, dtype: int64 kai telos insample Date
2022-05-25    4
2022-05-26    5
Name: URI, dtype: int64 mikos 20
--------------------------------------------------------------- False
5 defaultdict(<class 'int'>, {1: 7, 5: 4, 3: 3, 2: 2, 4: 4})
imera : 2022-05-31
arxi insample Date
2022-05-02    5
Name: URI, dtype: int64 kai telos insample Date
2022-05-26    5
2022-05-27    5
Name: URI, dtype: int64 mikos 20
--------------------------------------------------------------- False
5 defaultdict(<class 'int'>, {5: 5, 3: 3, 1: 6, 2: 2, 4: 4})
imera : 2022-06-01
arxi insample Date
2022-05-03    3
Name: URI, dtype: int64 kai telos insample Date
2022-05-27    5
2022-05-31    2
Name: URI, dtype: int64 mikos 20
--------------------------------------------------------------- False
2 defaultdict(<class 'int'>, {3: 3, 1: 6, 2: 3, 5: 4, 4: 4})
imera : 2022-06-02
arxi insample Date
2022-05-04    1
Name: URI, dtype

In [86]:
RPS_1m.mean(axis=1).mean()

0.16836592592592595

In [87]:
RPS_1m.mean(axis=1)

date
2022-05-23    0.180133
2022-05-24    0.140089
2022-05-25    0.157667
2022-05-26    0.182733
2022-05-27    0.169200
2022-05-31    0.170489
2022-06-01    0.182822
2022-06-02    0.169200
2022-06-03    0.152244
2022-06-06    0.156778
2022-06-07    0.171711
2022-06-08    0.171644
2022-06-09    0.152578
2022-06-10    0.163756
2022-06-13    0.175133
2022-06-14    0.159467
2022-06-15    0.166000
2022-06-16    0.166533
2022-06-17    0.176911
2022-06-21    0.166378
2022-06-22    0.174111
2022-06-23    0.159067
2022-06-24    0.162400
2022-06-27    0.174467
2022-06-28    0.178844
2022-06-29    0.171178
2022-06-30    0.155844
2022-07-01    0.186889
2022-07-05    0.171644
2022-07-06    0.169333
2022-07-07    0.173578
2022-07-08    0.156800
2022-07-11    0.198178
2022-07-12    0.191222
2022-07-13    0.169356
2022-07-14    0.155711
2022-07-15    0.171822
2022-07-18    0.163644
2022-07-19    0.173667
2022-07-20    0.166244
2022-07-21    0.166200
2022-07-22    0.160644
2022-07-25    0.169911
2022-0

#####Two Months
***

In [89]:
t_2m=pred(q2_2,186)
t_2m=pd.DataFrame.from_dict(t_2m)
t_2m.set_index('date')
RPS_2m= RPS_data(t_2m,rd)
RPS_2m= create_RPS(t_2m,RPS_2m)
RPS_2m
print(RPS_2m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
arxi insample Date
2022-03-31    2
Name: URI, dtype: int64 kai telos insample Date
2022-05-25    4
2022-05-26    5
Name: URI, dtype: int64 mikos 40
--------------------------------------------------------------- False
5 defaultdict(<class 'int'>, {2: 6, 1: 14, 4: 6, 5: 11, 3: 3})
imera : 2022-05-31
arxi insample Date
2022-04-01    1
Name: URI, dtype: int64 kai telos insample Date
2022-05-26    5
2022-05-27    5
Name: URI, dtype: int64 mikos 40
--------------------------------------------------------------- False
5 defaultdict(<class 'int'>, {1: 14, 4: 6, 5: 12, 2: 5, 3: 3})
imera : 2022-06-01
arxi insample Date
2022-04-04    1
Name: URI, dtype: int64 kai telos insample Date
2022-05-27    5
2022-05-31    2
Name: URI, dtype: int64 mikos 40
--------------------------------------------------------------- False
2 defaultdict(<class 'int'>, {1: 13, 4: 6, 5: 12, 2: 6, 3: 3})
imera : 2022-06-02
arxi insample Date
2022-04-05    1
Name: URI,

In [ ]:
RPS_2m.mean(axis=1).mean()

In [91]:
RPS_2m.mean(axis=1)

date
2022-05-23    0.182539
2022-05-24    0.138494
2022-05-25    0.147550
2022-05-26    0.168711
2022-05-27    0.159950
2022-05-31    0.162406
2022-06-01    0.181317
2022-06-02    0.167817
2022-06-03    0.153767
2022-06-06    0.156939
2022-06-07    0.157439
2022-06-08    0.167700
2022-06-09    0.159822
2022-06-10    0.163200
2022-06-13    0.176428
2022-06-14    0.163639
2022-06-15    0.166072
2022-06-16    0.168844
2022-06-17    0.176511
2022-06-21    0.163172
2022-06-22    0.159728
2022-06-23    0.153867
2022-06-24    0.161978
2022-06-27    0.173783
2022-06-28    0.170039
2022-06-29    0.169117
2022-06-30    0.156633
2022-07-01    0.176411
2022-07-05    0.166100
2022-07-06    0.159183
2022-07-07    0.165722
2022-07-08    0.161706
2022-07-11    0.172672
2022-07-12    0.176444
2022-07-13    0.171611
2022-07-14    0.166256
2022-07-15    0.167133
2022-07-18    0.155344
2022-07-19    0.164261
2022-07-20    0.157972
2022-07-21    0.153050
2022-07-22    0.166372
2022-07-25    0.168028
2022-0

#####Three Months 
***

In [92]:
t_3m=pred(q2_2,166)
t_3m=pd.DataFrame.from_dict(t_3m)
t_3m.set_index('date')
RPS_3m= RPS_data(t_3m,rd)
RPS_3m= create_RPS(t_3m,RPS_3m)
RPS_3m
print(RPS_3m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
arxi insample Date
2022-03-03    1
Name: URI, dtype: int64 kai telos insample Date
2022-05-25    4
2022-05-26    5
Name: URI, dtype: int64 mikos 60
--------------------------------------------------------------- False
5 defaultdict(<class 'int'>, {1: 17, 5: 16, 3: 5, 2: 10, 4: 12})
imera : 2022-05-31
arxi insample Date
2022-03-04    1
Name: URI, dtype: int64 kai telos insample Date
2022-05-26    5
2022-05-27    5
Name: URI, dtype: int64 mikos 60
--------------------------------------------------------------- False
5 defaultdict(<class 'int'>, {1: 16, 5: 17, 3: 5, 2: 10, 4: 12})
imera : 2022-06-01
arxi insample Date
2022-03-07    5
Name: URI, dtype: int64 kai telos insample Date
2022-05-27    5
2022-05-31    2
Name: URI, dtype: int64 mikos 60
--------------------------------------------------------------- False
2 defaultdict(<class 'int'>, {5: 17, 3: 5, 2: 11, 4: 12, 1: 15})
imera : 2022-06-02
arxi insample Date
2022-03-08    3
Name

In [93]:
RPS_3m.mean(axis=1).mean()

0.16156641975308644

In [94]:
RPS_3m.mean(axis=1)

date
2022-05-23    0.173817
2022-05-24    0.141943
2022-05-25    0.150412
2022-05-26    0.162304
2022-05-27    0.154765
2022-05-31    0.161884
2022-06-01    0.168047
2022-06-02    0.159284
2022-06-03    0.159812
2022-06-06    0.152612
2022-06-07    0.151462
2022-06-08    0.163321
2022-06-09    0.155222
2022-06-10    0.161281
2022-06-13    0.176323
2022-06-14    0.165259
2022-06-15    0.171440
2022-06-16    0.174575
2022-06-17    0.175760
2022-06-21    0.149049
2022-06-22    0.156891
2022-06-23    0.147491
2022-06-24    0.171583
2022-06-27    0.165993
2022-06-28    0.167286
2022-06-29    0.163588
2022-06-30    0.163138
2022-07-01    0.176415
2022-07-05    0.169825
2022-07-06    0.152585
2022-07-07    0.159775
2022-07-08    0.154798
2022-07-11    0.173965
2022-07-12    0.166647
2022-07-13    0.168748
2022-07-14    0.169346
2022-07-15    0.167022
2022-07-18    0.148314
2022-07-19    0.159069
2022-07-20    0.149998
2022-07-21    0.144798
2022-07-22    0.160709
2022-07-25    0.165783
2022-0

#####Six Months 
***

In [95]:
t_6m=pred(q2_2,106)
t_6m=pd.DataFrame.from_dict(t_6m)
t_6m.set_index('date')
RPS_6m= RPS_data(t_6m,rd)
RPS_6m= create_RPS(t_6m,RPS_6m)
RPS_6m
print(RPS_6m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
arxi insample Date
2021-12-06    5
Name: URI, dtype: int64 kai telos insample Date
2022-05-25    4
2022-05-26    5
Name: URI, dtype: int64 mikos 120
--------------------------------------------------------------- False
5 defaultdict(<class 'int'>, {5: 33, 3: 14, 4: 19, 1: 36, 2: 18})
imera : 2022-05-31
arxi insample Date
2021-12-07    3
Name: URI, dtype: int64 kai telos insample Date
2022-05-26    5
2022-05-27    5
Name: URI, dtype: int64 mikos 120
--------------------------------------------------------------- False
5 defaultdict(<class 'int'>, {3: 14, 4: 19, 1: 36, 5: 33, 2: 18})
imera : 2022-06-01
arxi insample Date
2021-12-08    4
Name: URI, dtype: int64 kai telos insample Date
2022-05-27    5
2022-05-31    2
Name: URI, dtype: int64 mikos 120
--------------------------------------------------------------- False
2 defaultdict(<class 'int'>, {4: 19, 1: 36, 3: 13, 5: 33, 2: 19})
imera : 2022-06-02
arxi insample Date
2021-12-09    

In [96]:
RPS_6m.mean(axis=1).mean()

0.1603870781893004

In [97]:
RPS_6m.mean(axis=1)

date
2022-05-23    0.172406
2022-05-24    0.145376
2022-05-25    0.147252
2022-05-26    0.162141
2022-05-27    0.154306
2022-05-31    0.161248
2022-06-01    0.177106
2022-06-02    0.159187
2022-06-03    0.162257
2022-06-06    0.152598
2022-06-07    0.150276
2022-06-08    0.162020
2022-06-09    0.158787
2022-06-10    0.166070
2022-06-13    0.168449
2022-06-14    0.160768
2022-06-15    0.168827
2022-06-16    0.169310
2022-06-17    0.176425
2022-06-21    0.149205
2022-06-22    0.147635
2022-06-23    0.149723
2022-06-24    0.168436
2022-06-27    0.167170
2022-06-28    0.161630
2022-06-29    0.167075
2022-06-30    0.163483
2022-07-01    0.172143
2022-07-05    0.166223
2022-07-06    0.149998
2022-07-07    0.156765
2022-07-08    0.148944
2022-07-11    0.174238
2022-07-12    0.163363
2022-07-13    0.169709
2022-07-14    0.170366
2022-07-15    0.162102
2022-07-18    0.145390
2022-07-19    0.159073
2022-07-20    0.147641
2022-07-21    0.148470
2022-07-22    0.160768
2022-07-25    0.164169
2022-0

#####All the samples
***

In [98]:
t_all=pred2(q2_2)
t_all=pd.DataFrame.from_dict(t_all)
t_all.set_index('date')
RPS_all= RPS_data(t_all,rd)
RPS_all= create_RPS(t_all,RPS_all)
RPS_all
print(RPS_all.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
[datetime.date(2022, 5, 24), datetime.date(2022, 5, 25), datetime.date(2022, 5, 26), datetime.date(2022, 5, 27), datetime.date(2022, 5, 31), datetime.date(2022, 6, 1), datetime.date(2022, 6, 2), datetime.date(2022, 6, 3), datetime.date(2022, 6, 6), datetime.date(2022, 6, 7), datetime.date(2022, 6, 8), datetime.date(2022, 6, 9), datetime.date(2022, 6, 10), datetime.date(2022, 6, 13), datetime.date(2022, 6, 14), datetime.date(2022, 6, 15), datetime.date(2022, 6, 16), datetime.date(2022, 6, 17), datetime.date(2022, 6, 21), datetime.date(2022, 6, 22), datetime.date(2022, 6, 23), datetime.date(2022, 6, 24), datetime.date(2022, 6, 27), datetime.date(2022, 6, 28), datetime.date(2022, 6, 29), datetime.date(2022, 6, 30), datetime.date(2022, 7, 1), datetime.date(2022, 7, 5), datetime.date(2022, 7, 6), datetime.date(2022, 7, 7), datetime.date(2022, 7, 8), datetime.date(2022, 7, 11), datetime.date(2022, 7, 12), datetime.date(2022, 7, 13), date

In [99]:
RPS_all.mean(axis=1).mean()

0.15878366522637846

In [100]:
RPS_all.mean(axis=1)

date
2022-05-24    0.151833
2022-05-25    0.152886
2022-05-26    0.157999
2022-05-27    0.154062
2022-05-31    0.161877
2022-06-01    0.166242
2022-06-02    0.155264
2022-06-03    0.160546
2022-06-06    0.153595
2022-06-07    0.152332
2022-06-08    0.159763
2022-06-09    0.159213
2022-06-10    0.161774
2022-06-13    0.164495
2022-06-14    0.162270
2022-06-15    0.162983
2022-06-16    0.163562
2022-06-17    0.167241
2022-06-21    0.151228
2022-06-22    0.152884
2022-06-23    0.151968
2022-06-24    0.163685
2022-06-27    0.162264
2022-06-28    0.161312
2022-06-29    0.164036
2022-06-30    0.161202
2022-07-01    0.165019
2022-07-05    0.161838
2022-07-06    0.150860
2022-07-07    0.157712
2022-07-08    0.150776
2022-07-11    0.166195
2022-07-12    0.162296
2022-07-13    0.165427
2022-07-14    0.166437
2022-07-15    0.161881
2022-07-18    0.148855
2022-07-19    0.157706
2022-07-20    0.150405
2022-07-21    0.149175
2022-07-22    0.160418
2022-07-25    0.163487
2022-07-26    0.164270
2022-0